# METER DATA LOGIC

# Import and Load Data

In [1]:
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
import meterdatalogic as ml

### From Dataframe

In [2]:
TZ = "Australia/Brisbane"

# 7 days of half-hourly data for one NMI
rng = pd.date_range("2025-01-01", periods=48*7, freq="30min", tz=TZ)
raw = pd.DataFrame({
    "t_start": rng,
    "nmi": "Q1234567890",
    "channel": "E1",
    "kwh": 0.5
})
raw.head()

df = ml.ingest.from_dataframe(raw, tz=TZ)
ml.validate.assert_canon(df)
df

/Users/tyler/Developer/mdt-django-poc/meterdatalogic/meterdatalogic/ingest.py:30: FutureWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  .apply(_infer_group_cadence)


nmi channel         flow  kwh  cadence_min
t_start                                                                      
2025-01-01 00:00:00+10:00  Q1234567890      E1  grid_import  0.5           30
2025-01-01 00:30:00+10:00  Q1234567890      E1  grid_import  0.5           30
2025-01-01 01:00:00+10:00  Q1234567890      E1  grid_import  0.5           30
2025-01-01 01:30:00+10:00  Q1234567890      E1  grid_import  0.5           30
2025-01-01 02:00:00+10:00  Q1234567890      E1  grid_import  0.5           30
...                                ...     ...          ...  ...          ...
2025-01-07 21:30:00+10:00  Q1234567890      E1  grid_import  0.5           30
2025-01-07 22:00:00+10:00  Q1234567890      E1  grid_import  0.5           30
2025-01-07 22:30:00+10:00  Q1234567890      E1  grid_import  0.5           30
2025-01-07 23:00:00+10:00  Q1234567890      E1  grid_import  0.5           30
2025-01-07 23:30:00+10:00  Q1234567890      E1  grid_import  0.5           30

[336 rows x 5 columns]

### From NEM12 File

In [3]:
### This is a manual overview of NEM12 ingestion. The actual test is in test_ingest.py
# from nemreader import NEMFile
# nem_file = NEMFile("./data/Example_NEM12_ManyNMIs.zip")
# df = nem_file.get_data_frame()
# df

In [12]:
# df = ml.ingest.from_nem12("./data/unzipped/Example_NEM12_month_solar.csv", tz="Australia/Brisbane")
# df = ml.ingest.from_nem12("./data/Sample1.csv", tz="Australia/Brisbane")
df = ml.ingest.from_nem12("./data/QB00000001_20250101_20251031_20251107130416_ENERGEXP_DETAILED.csv", tz="Australia/Brisbane")
# df = ml.ingest.from_nem12("./data/Example_NEM12_ManyNMIs.zip", tz="Australia/Brisbane", nmi="nmi90")
ml.validate.assert_canon(df)
bands = [
    {"name": "off", "start": "00:00", "end": "16:00"},
    {"name": "peak", "start": "16:00", "end": "21:00"},
    {"name": "shoulder", "start": "21:00", "end": "24:00"},
]
df

/Users/tyler/Developer/mdt-django-poc/meterdatalogic/meterdatalogic/ingest.py:30: FutureWarning:

DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.



nmi channel               flow     kwh  \
t_start                                                                    
2025-01-01 00:00:00+10:00  QB00000001      B1  grid_export_solar  0.0000   
2025-01-01 00:00:00+10:00  QB00000001      E1        grid_import  0.0257   
2025-01-01 00:05:00+10:00  QB00000001      E1        grid_import  0.0174   
2025-01-01 00:05:00+10:00  QB00000001      B1  grid_export_solar  0.0000   
2025-01-01 00:10:00+10:00  QB00000001      B1  grid_export_solar  0.0000   
...                               ...     ...                ...     ...   
2025-10-30 23:45:00+10:00  QB00000001      B1  grid_export_solar  0.0000   
2025-10-30 23:50:00+10:00  QB00000001      E1        grid_import  0.0469   
2025-10-30 23:50:00+10:00  QB00000001      B1  grid_export_solar  0.0000   
2025-10-30 23:55:00+10:00  QB00000001      B1  grid_export_solar  0.0000   
2025-10-30 23:55:00+10:00  QB00000001      E1        grid_import  0.0400   

                           cadence_min  
t_start                                 
2025-01-01 00:00:00+10:00            5  
2025-01-01 00:00:00+10:00            5  
2025-01-01 00:05:00+10:00            5  
2025-01-01 00:05:00+10:00            5  
2025-01-01 00:10:00+10:00            5  
...                                ...  
2025-10-30 23:45:00+10:00            5  
2025-10-30 23:50:00+10:00            5  
2025-10-30 23:50:00+10:00            5  
2025-10-30 23:55:00+10:00            5  
2025-10-30 23:55:00+10:00            5  

[174528 rows x 5 columns]

In [13]:
ml.summary.summarise(df)

{'meta': {'nmis': 1,
  'start': '2025-01-01 00:00:00+10:00',
  'end': '2025-10-30 23:55:00+10:00',
  'cadence_min': 5,
  'days': 303,
  'channels': ['B1', 'E1'],
  'flows': ['grid_export_solar', 'grid_import']},
 'energy': {'grid_export_solar': 779.6623, 'grid_import': 5231.7955},
 'per_day_avg_kwh': 19.839794719471946,
 'peaks': {'max_interval_kwh': 0.7297,
  'max_interval_time': '2025-09-14T15:45:00+10:00'},
 'profile24': [{'slot': '00:00',
   'grid_export_solar': 0.0,
   'grid_import': 0.05104686468646865},
  {'slot': '00:05',
   'grid_export_solar': 0.0,
   'grid_import': 0.04774785478547854},
  {'slot': '00:10',
   'grid_export_solar': 0.0,
   'grid_import': 0.04585676567656766},
  {'slot': '00:15',
   'grid_export_solar': 0.0,
   'grid_import': 0.04422871287128713},
  {'slot': '00:20',
   'grid_export_solar': 0.0,
   'grid_import': 0.04276699669966996},
  {'slot': '00:25',
   'grid_export_solar': 0.0,
   'grid_import': 0.04156270627062707},
  {'slot': '00:30',
   'grid_export_sol

# Visualisations

In [14]:
hist = (
    df.reset_index()[["t_start","flow","kwh"]]
      .sort_values("t_start")
)

fig = px.area(
    hist, x="t_start", y="kwh", color="flow",
    title="Historical Interval Energy (kWh) by Flow",
    labels={"t_start":"Time", "kwh":"kWh"}
)
fig.update_layout(legend_title_text="Flow", hovermode="x unified")
fig.show()


In [15]:
daily = ml.transform.aggregate(df, freq="1D", groupby="flow", pivot=True)
# Convert to tidy for plotting
daily = daily.reset_index().rename(columns={"t_start": "day"})
daily = daily.melt(id_vars="day", var_name="flow", value_name="kwh")

fig = px.bar(
    daily, x="day", y="kwh", color="flow",
    title="Daily Energy by Flow",
    labels={"day":"Day","kwh":"kWh"}
)
fig.update_layout(hovermode="x unified")
fig.show()


In [16]:
monthly = ml.transform.aggregate(df, freq="1MS", groupby="flow", pivot=True)
monthly = monthly.reset_index().rename(columns={"t_start": "month"})
monthly["month"] = ml.utils.month_label(monthly["month"]).astype(str)

melted = monthly.melt(id_vars="month", var_name="flow", value_name="kwh")

fig = px.bar(
    melted, x="month", y="kwh", color="flow",
    title="Monthly Energy by Flow",
    labels={"month":"Month","kwh":"kWh"},
    barmode="stack"
)
fig.update_layout(hovermode="x unified")
fig.show()


In [18]:
# Average 24-Hour Profile (kWh per interval) by flow
_prof = df.copy()
_prof["slot"] = pd.DatetimeIndex(_prof.index).strftime("%H:%M")
prof = (
    _prof.groupby(["slot", "flow"])['kwh']
        .mean()
        .unstack("flow")
        .fillna(0.0)
        .reset_index()
)

melted = prof.melt(id_vars="slot", var_name="flow", value_name="kwh")

fig = px.line(
    melted, x="slot", y="kwh", color="flow",
    title="Average 24-Hour Profile (kWh per interval)",
    labels={"slot":"Time of Day","kwh":"kWh per interval"}
)
fig.update_xaxes(type="category", tickangle=-45)
fig.update_layout(hovermode="x unified")
fig.show()


In [19]:
tou = ml.transform.tou_bins(df[df["flow"]=="grid_import"], bands)  # month + off/peak/shoulder
melted = tou.melt(id_vars="month", var_name="band", value_name="kwh")

fig = px.bar(
    melted, x="month", y="kwh", color="band",
    title="Monthly Import by ToU Band",
    labels={"month":"Month","kwh":"kWh"},
    barmode="stack"
)
fig.update_layout(hovermode="x unified")
fig.show()


In [20]:
demand = ml.transform.aggregate(
    df,
    freq="1MS",
    flows=["grid_import"],
    metric="kW",
    stat="max",
    out_col="demand_kw",
    window_start="16:00",
    window_end="21:00",
    window_days="MF",
)
# Add month label for plotting
_plot = demand.copy()
_plot["month"] = ml.utils.month_label(_plot.index).astype(str)

fig = px.bar(_plot, x="month", y="demand_kw",
             title="Monthly Peak Demand (kW) in Window (MF 16:00–21:00)",
             labels={"month":"Month","demand_kw":"kW"})
fig.update_layout(hovermode="x unified")
fig.show()


In [21]:
## My current plan 
plan = ml.types.Plan(
    usage_bands=[
        ml.types.ToUBand(
            name="all_times",     # must match the column name produced by transform.tou_bins
            start="00:00",
            end="24:00",          # full-day window
            rate_c_per_kwh=43.25  # $0.4325/kWh -> 43.25 cents
        )
    ],
    fixed_c_per_day=170.56,        # $1.7056/day -> 170.56 cents
    feed_in_c_per_kwh=60.0,        # $0.60/kWh -> 60.0 cents
    demand=None                    # no demand charge on this plan
)
bill = ml.pricing.compute_billables(df, plan, mode="monthly")
cost = ml.pricing.estimate_costs(bill, plan)  # month, components, total
cost



month  energy_cost  demand_cost  fixed_cost  feed_in_credit  \
0  2025-01   263.413174          0.0     52.8736       -54.09420   
1  2025-02   226.800232          0.0     47.7568       -54.63738   
2  2025-03   190.096379          0.0     52.8736       -46.31646   
3  2025-04   218.933317          0.0     51.1680       -45.14568   
4  2025-05   179.510163          0.0     52.8736       -37.30284   
5  2025-06   224.507895          0.0     51.1680       -29.32494   
6  2025-07   329.631821          0.0     52.8736       -29.02110   
7  2025-08   242.318116          0.0     52.8736       -43.14612   
8  2025-09   181.074472          0.0     51.1680       -70.29498   
9  2025-10   206.465985          0.0     52.8736       -58.51368   

   pay_on_time_discount  gst       total  
0                  -0.0  0.0  262.192574  
1                  -0.0  0.0  219.919652  
2                  -0.0  0.0  196.653519  
3                  -0.0  0.0  224.955636  
4                  -0.0  0.0  195.080923  
5                  -0.0  0.0  246.350955  
6                  -0.0  0.0  353.484321  
7                  -0.0  0.0  252.045596  
8                  -0.0  0.0  161.947492  
9                  -0.0  0.0  200.825905

In [22]:
plan = ml.types.Plan(
    usage_bands=[
        ml.types.ToUBand("off", "00:00", "16:00", 22.0),
        ml.types.ToUBand("peak","16:00", "21:00", 45.0),
        ml.types.ToUBand("shoulder","21:00", "24:00", 28.0),
    ],
    demand=ml.types.DemandCharge("16:00","21:00","MF", 12.0),
    fixed_c_per_day=95.0,
    feed_in_c_per_kwh=6.0
)

bill = ml.pricing.compute_billables(df, plan, mode="monthly")
cost = ml.pricing.estimate_costs(bill, plan)  # month, components, total
cost



month  energy_cost  demand_cost  fixed_cost  feed_in_credit  \
0  2025-01   205.814847      75.6000       29.45       -5.409420   
1  2025-02   170.661649      96.1920       26.60       -5.463738   
2  2025-03   134.109958      69.2928       29.45       -4.631646   
3  2025-04   162.443036      80.5104       28.50       -4.514568   
4  2025-05   131.699066      71.2080       29.45       -3.730284   
5  2025-06   154.930058      79.7040       28.50       -2.932494   
6  2025-07   238.650303      90.8352       29.45       -2.902110   
7  2025-08   172.532226      80.4096       29.45       -4.314612   
8  2025-09   134.352851      87.1776       28.50       -7.029498   
9  2025-10   156.774958      80.0352       29.45       -5.851368   

   pay_on_time_discount  gst       total  
0                  -0.0  0.0  305.455427  
1                  -0.0  0.0  287.989911  
2                  -0.0  0.0  228.221112  
3                  -0.0  0.0  266.938868  
4                  -0.0  0.0  228.626782  
5                  -0.0  0.0  260.201564  
6                  -0.0  0.0  356.033393  
7                  -0.0  0.0  278.077214  
8                  -0.0  0.0  243.000953  
9                  -0.0  0.0  260.408790

In [23]:
melted = cost.melt(id_vars="month", value_vars=["energy_cost","demand_cost","fixed_cost","feed_in_credit"],
                   var_name="component", value_name="AUD")

fig = px.bar(
    melted, x="month", y="AUD", color="component",
    title="Monthly Cost Breakdown",
    labels={"month":"Month","AUD":"$"},
    barmode="relative"  # feed_in_credit is negative → subtracts
)
# Optional: add total as line
fig2 = go.Figure(fig.data)
fig2.add_trace(go.Scatter(x=cost["month"], y=cost["total"], name="Total", mode="lines+markers"))
fig2.update_layout(title="Monthly Cost Breakdown (+ Total)", hovermode="x unified")
fig2.show()

In [24]:
g = df.copy()
g["weekday"] = g.index.weekday  # 0=Mon
g["hour"] = g.index.hour
heat = g.groupby(["weekday","hour"])["kwh"].mean().reset_index()

fig = px.density_heatmap(
    heat, x="hour", y="weekday", z="kwh",
    title="Average kWh by Hour × Weekday",
    labels={"hour":"Hour of Day","weekday":"Day (0=Mon)","kwh":"kWh per interval"},
    nbinsx=24, nbinsy=7, histfunc="avg", color_continuous_scale="Viridis"
)
fig.update_yaxes(dtick=1)
fig.show()


# Scenario Modelling

In [25]:
import pandas as pd
import meterdatalogic as ml
from meterdatalogic.scenario import run
from meterdatalogic.types import EVConfig, PVConfig, BatteryConfig

# Plan for costs (optional)
plan = ml.types.Plan(
    usage_bands=[
        ml.types.ToUBand("off","00:00","16:00",22.0),
        ml.types.ToUBand("peak","16:00","21:00",45.0),
        ml.types.ToUBand("shoulder","21:00","24:00",28.0),
    ],
    demand=ml.types.DemandCharge("16:00","21:00","MF",12.0),
    fixed_c_per_day=95.0,
    feed_in_c_per_kwh=6.0
)

# Scenario configs
ev_cfg = EVConfig(daily_kwh=8.0, max_kw=7.0, window_start="18:00", window_end="22:00", days="ALL", strategy="immediate")
pv_cfg = PVConfig(system_kwp=6.6, inverter_kw=5.0, loss_fraction=0.15)
bat_cfg = BatteryConfig(capacity_kwh=10.0, max_kw=5.0, round_trip_eff=0.9, soc_min=0.1, soc_max=0.95)

# Run scenario
result = run(df, ev=ev_cfg, pv=pv_cfg, battery=bat_cfg, plan=plan)

print("Δ Import (kWh):", round(result.delta["import_kwh_delta"], 2))
print("Δ Export (kWh):", round(result.delta["export_kwh_delta"], 2))
print("Δ Cost ($):", None if result.delta["cost_total_delta"] is None else round(result.delta["cost_total_delta"], 2))
print("Explain:", {k: round(v,2) if isinstance(v,(int,float)) and v is not None else v for k,v in result.explain.items()})

Δ Import (kWh): 1613.28
Δ Export (kWh): 20927.46
Δ Cost ($): 7.22
Explain: {'ev_kwh': 2424.0, 'pv_kwh': 23698.66, 'battery_discharge_kwh': 2491.65, 'battery_charge_kwh': 2768.5, 'battery_cycles_est': 249.17, 'pv_self_consumption_pct': 14.98}


In [26]:
# Optional: charts (Plotly)
import plotly.express as px

before = ml.transform.aggregate(result.df_before, freq="1MS", groupby="flow", pivot=True)
before = before.reset_index().rename(columns={"t_start": "month"})
before["month"] = ml.utils.month_label(before["month"]).astype(str)
before_m = before.melt(id_vars="month", var_name="flow", value_name="kwh")

after = ml.transform.aggregate(result.df_after, freq="1MS", groupby="flow", pivot=True)
after = after.reset_index().rename(columns={"t_start": "month"})
after["month"] = ml.utils.month_label(after["month"]).astype(str)
after_m = after.melt(id_vars="month", var_name="flow", value_name="kwh")

before_m["scenario"] = "before"; after_m["scenario"] = "after"
both = pd.concat([before_m, after_m], ignore_index=True)

fig = px.bar(both, x="month", y="kwh", color="flow", facet_row="scenario",
             barmode="stack", title="Monthly Energy by Flow — Before vs After")
fig.show()


In [27]:
# Average 24-hour profile: baseline vs scenario (overlayed)
# — shows import/export as separate traces, plus an optional "net" line.

import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go

try:
    import meterlogic as ml
except ImportError:
    import meterdatalogic as ml

def plot_avg_profile_before_after(df_before: pd.DataFrame,
                                  df_after: pd.DataFrame,
                                  *,
                                  show_net: bool = True,
                                  title: str = "Average 24-Hour Profile — Before vs After"):
    """
    Overlays baseline and scenario average day profiles.
    - Uses ml.transform.profile24() to compute kWh per interval slot (mean across days)
    - Plots grid_import and grid_export_solar as separate traces
    - Optionally adds a 'net' line (import - export) for each scenario
    """
    # Compute profile (slot + columns per flow)
    prof_b = ml.transform.profile24(df_before)  # columns: slot, grid_import, grid_export_solar, ...
    prof_a = ml.transform.profile24(df_after)

    # Ensure both have the same slot ordering (categorical 00:00..23:30)
    slots = prof_b["slot"].unique().tolist()
    prof_a = prof_a.set_index("slot").reindex(slots).reset_index()

    # Helper to build a tidy frame with optional net
    def melt_with_net(prof: pd.DataFrame, label: str) -> pd.DataFrame:
        flows = [c for c in prof.columns if c != "slot"]
        tidy = prof.melt(id_vars="slot", value_vars=flows, var_name="flow", value_name="kwh")
        tidy["scenario"] = label

        if show_net:
            imp = prof.get("grid_import", pd.Series(0.0, index=prof.index))
            exp = prof.get("grid_export_solar", pd.Series(0.0, index=prof.index))
            net = imp - exp  # positive = net import, negative = net export
            tidy = pd.concat([
                tidy,
                pd.DataFrame({"slot": prof["slot"], "flow": "net", "kwh": net, "scenario": label})
            ], ignore_index=True)

        return tidy

    tb = melt_with_net(prof_b, "before")
    ta = melt_with_net(prof_a, "after")
    both = pd.concat([tb, ta], ignore_index=True)

    # Optional: flip export sign so export appears below zero (purely visual)
    both["kwh_plot"] = np.where(both["flow"].str.contains("export"), -both["kwh"], both["kwh"])

    # Build the figure: overlay 'before' and 'after'
    fig = go.Figure()

    def add_lines(df_scn, name_suffix, dash=None, width=2):
        for flow_name in sorted(df_scn["flow"].unique()):
            sub = df_scn[df_scn["flow"] == flow_name]
            fig.add_trace(go.Scatter(
                x=sub["slot"], y=sub["kwh_plot"],
                mode="lines",
                name=f"{flow_name} ({name_suffix})",
                line=dict(dash=dash, width=width)
            ))

    add_lines(both[both["scenario"] == "before"], "before", dash="dot", width=2)
    add_lines(both[both["scenario"] == "after"],  "after",  dash=None,   width=3)

    fig.update_layout(
        title=title,
        xaxis_title="Time of Day",
        yaxis_title="kWh per interval",
        hovermode="x unified",
        legend_title_text="Series",
    )
    fig.update_xaxes(type="category", tickangle=-45)
    fig.add_hline(y=0, line_color="black", line_width=0.6)

    return fig

# --- Usage example ---
# Assuming you already have `result = run(df, ev=..., pv=..., battery=..., plan=...)`:
fig = plot_avg_profile_before_after(result.df_before, result.df_after, show_net=True)
fig.show()


AttributeError: module 'meterdatalogic.transform' has no attribute 'profile24'

In [ ]:
import plotly.graph_objects as go
import pandas as pd

# Convert profile24 lists to DataFrames if they come as lists of dicts
df_before = pd.DataFrame(result.summary_before["profile24"])
df_after = pd.DataFrame(result.summary_after["profile24"])

# Ensure slot (HH:MM) column is sorted in time order
df_before = df_before.sort_values("slot")
df_after = df_after.sort_values("slot")

# Create Plotly figure
fig = go.Figure()

fig.add_trace(go.Scatter(
    x=df_before["slot"],
    y=df_before["grid_import"],
    mode="lines+markers",
    name="Before Scenario",
    line=dict(color="royalblue"),
    marker=dict(size=4)
))

fig.add_trace(go.Scatter(
    x=df_after["slot"],
    y=df_after["grid_import"],
    mode="lines+markers",
    name="After Scenario",
    line=dict(color="orange"),
    marker=dict(size=4)
))

fig.update_layout(
    title="Average Daily Profile – Before vs After Scenario",
    xaxis_title="Time of Day",
    yaxis_title="Grid Import (kWh per 30-min interval)",
    template="plotly_white",
    hovermode="x unified",
    legend=dict(x=0.02, y=0.98)
)

fig.show()


In [ ]:
import pandas as pd
import plotly.graph_objects as go
from meterdatalogic.scenario import _apply_ev, _apply_pv, _apply_battery_self_consume, EVConfig, PVConfig, BatteryConfig

def build_solar_soak_timeseries(df, ev_cfg, pv_cfg, bat_cfg):
    """
    Recompute scenario components to visualise PV allocation (per-interval).
    Returns a tidy DataFrame with:
      - pv_gen_kwh, pv_to_load_kwh, pv_to_battery_kwh, pv_export_kwh
      - load_total_kwh (baseline + EV), grid_import_after_kwh
      - battery_discharge_kwh, battery_soc_kwh
    """
    # --- Baseline import/export series (per your canon) ---
    def _collapse_flows(df):
        idx_full = df.index
        flows = df["flow"].astype(str)
        df_imp = df.loc[flows.str.contains("import", na=False)]
        df_exp = df.loc[flows.str.contains("export", na=False)]
        imp = df_imp.groupby(level=0)["kwh"].sum() if not df_imp.empty else pd.Series(dtype=float)
        exp = df_exp.groupby(level=0)["kwh"].sum() if not df_exp.empty else pd.Series(dtype=float)
        imp = imp.reindex(idx_full, fill_value=0.0).sort_index()
        exp = exp.reindex(idx_full, fill_value=0.0).sort_index()
        return imp, exp

    # Interval hours from canon
    cmin = int(df["cadence_min"].iloc[0]) if len(df) else 30
    interval_h = cmin / 60.0

    s_import0, s_export0 = _collapse_flows(df)
    idx = s_import0.index

    # EV load (kWh/interval)
    ev_series = _apply_ev(idx, ev_cfg, interval_h) if ev_cfg else pd.Series(0.0, index=idx)
    load_total = (s_import0 + ev_series).to_numpy()  # local load before PV/battery

    # PV generation (kWh/interval)
    pv_series = _apply_pv(idx, pv_cfg, interval_h) if pv_cfg else pd.Series(0.0, index=idx)
    pv_arr = pv_series.to_numpy()

    # PV allocation before battery: self-consume vs leftover
    pv_to_load = np.minimum(pv_arr, load_total)
    pv_leftover = pv_arr - pv_to_load  # candidate for battery charge or export

    # Import before battery (still needed after PV-to-load)
    import_prebat = load_total - pv_to_load
    export_prebat = s_export0.to_numpy() + pv_leftover.copy()

    # Battery (self consume)
    bat_dis = bat_ch = soc = np.zeros(len(idx))
    if bat_cfg and bat_cfg.capacity_kwh > 0 and bat_cfg.max_kw > 0:
        bat_dis, bat_ch, soc = _apply_battery_self_consume(
            import_prebat=import_prebat,
            pv_excess_prebat=pv_leftover,
            cfg=bat_cfg,
            interval_h=interval_h,
        )
        # export_prebat already reduced inside dispatcher via pv_leftover mutation

    # After-battery import/export
    grid_import_after = pd.Series(import_prebat, index=idx)
    pv_export_after = pd.Series(export_prebat, index=idx)

    # PV-to-battery is exactly battery charge energy (from PV excess by design)
    pv_to_battery = pd.Series(bat_ch, index=idx)

    out = pd.DataFrame({
        "pv_gen_kwh": pv_series,
        "pv_to_load_kwh": pd.Series(pv_to_load, index=idx),
        "pv_to_battery_kwh": pv_to_battery,
        "pv_export_kwh": pv_export_after,
        "load_total_kwh": pd.Series(load_total, index=idx),
        "grid_import_after_kwh": grid_import_after,
        "battery_discharge_kwh": pd.Series(bat_dis, index=idx),
        "battery_soc_kwh": pd.Series(soc, index=idx),
    })
    return out

def solar_soak_profile_plot(df, ev_cfg, pv_cfg, bat_cfg, title="Solar Soak – Average Day"):
    """
    Builds an average-day (HH:MM) plot showing PV allocation: PV->Load, PV->Battery, PV->Export (stacked area),
    with lines for Load Total and Grid Import (after battery).
    """
    ts = build_solar_soak_timeseries(df, ev_cfg, pv_cfg, bat_cfg)
    # Average by slot (time-of-day). We’ll build a "slot" column first.
    local = ts.index.tz_convert(ts.index.tz)
    slot = local.strftime("%H:%M")
    prof = ts.copy()
    prof["slot"] = slot
    g = prof.groupby("slot", sort=True).mean(numeric_only=True).reset_index()

    # Order slots chronologically (string sorting works for HH:MM)
    g = g.sort_values("slot")

    fig = go.Figure()

    # Stacked areas for PV allocation
    fig.add_trace(go.Scatter(
        x=g["slot"], y=g["pv_to_load_kwh"],
        name="PV → Load",
        mode="lines",
        stackgroup="pv", groupnorm="",
        hovertemplate="PV → Load: %{y:.3f} kWh<extra></extra>"
    ))
    fig.add_trace(go.Scatter(
        x=g["slot"], y=g["pv_to_battery_kwh"],
        name="PV → Battery",
        mode="lines",
        stackgroup="pv",
        hovertemplate="PV → Battery: %{y:.3f} kWh<extra></extra>"
    ))
    fig.add_trace(go.Scatter(
        x=g["slot"], y=g["pv_export_kwh"],
        name="PV → Export",
        mode="lines",
        stackgroup="pv",
        hovertemplate="PV → Export: %{y:.3f} kWh<extra></extra>"
    ))

    # Overlay lines for load & grid import after battery
    fig.add_trace(go.Scatter(
        x=g["slot"], y=g["load_total_kwh"],
        name="Load (Baseline + EV)",
        mode="lines+markers",
        hovertemplate="Load: %{y:.3f} kWh<extra></extra>"
    ))
    fig.add_trace(go.Scatter(
        x=g["slot"], y=g["grid_import_after_kwh"],
        name="Grid Import (After Battery)",
        mode="lines+markers",
        hovertemplate="Grid Import: %{y:.3f} kWh<extra></extra>"
    ))

    fig.update_layout(
        title=title,
        xaxis_title="Time of Day",
        yaxis_title="Energy per interval (kWh)",
        template="plotly_white",
        hovermode="x unified",
        legend=dict(x=0.02, y=0.98)
    )
    return fig

# Example usage:
fig = solar_soak_profile_plot(df, ev_cfg, pv_cfg, bat_cfg)
fig.show()
